In [28]:
from core import *
from modelparamgrid import *

C:\Users\tikyn\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\aeon\base\__init__.py:24: FutureWarning: The aeon package will soon be releasing v1.0.0 with the removal of legacy modules and interfaces such as BaseTransformer and BaseForecaster. This will contain breaking changes. See aeon-toolkit.org for more information. Set aeon.AEON_DEPRECATION_WARNING or the AEON_DEPRECATION_WARNING environmental variable to 'False' to disable this warning.
  warnings.warn(


<b>The whole model works in this order</b>
<ol>
    <li>clasp model - in: features ts [21][98][n] - out: prediction [20][21][98][m] - n>m</li>
    <ul>
        <li>21 video, ogni video 98 timeseries</li>
        <li>per ogni 98 timeseries, 98 prediction</li>
        <li>n = lunghezza timeseries</li>
        <li>m = numeri dei prediction</li>
    </ul>
    <li>split saliency - in: prediction [20][21][98][m] - out: pred_split [20][21][6][k][m]</li>
    <ul>
        <li>98 prediction divisi in 6 gruppi di k elementi. Possono esserci ripetizioni. 6*k > 98</li>
        <li>k = numero di prediction in un gruppo
    </ul>
    <li>combinesinglesaliency - in: pred_split[20][21][6][k][m] - out: salience_preds [20][21][6][x] - k>x</li>
    <ul>
        <li>ogni k prediction unite in 1 array e applicato MajorityVote</li>
        <li>x = MajorityVote genera la media di gruppi di prediction k</li>
    </ul>
    <li>union salience_preds - in: salience_preds [20][21][6][x] - out: union_pred [20][21][y] - y>x</li>
    <ul>
        <li>Le 6 salienze unite in un unico array</li>
        <li>y = unione di x
    </ul>
    <li>ignorezone - in: union_pred [20][21][y] - out: ignored_pred [20][21][a] - y>a</li>
    <ul>
        <li>Ignora le zone non annotate perchè fuori dal nostro use case</li>
        <li>a = numero di prediction dopo aver tolto i prediction dalle zone non annotate</li>
    </ul>
    <li>delnear - in: ignored_pred [20][21][a] - out: del_pred [20][21][b]</li>
    <ul>
        <li>Come MajorityVote ma lascia primo e ultimo del gruppo</li>
        <li>b = numero di prediction che delineano inizio e fine di movimenti</li>
    </ul>
    <li>DTW - in: del_pred [20][21][b] - out: dtw_pred [20][21][c] - b>c</li>
    <ul>
        <li>applico DTW per controllare se i prediction b hanno FP (false positive)</li>
        <li>c = numero di prediction con meno FP</li>
    </ul>
    <li>scoring - in: dtw_pred [20][21][c] - out: f1score [20][21]</li>
    <ul>
        <li>Per ogni prediction lungo c nei 21 video, calcolo lo score</li>
    </ul>
</ol>

This project is divided into three part, because each part takes a lot of days for computing the result:
<ol>
    <li>Clasp Model: (1) -> create all prediction from the clasp model</li>
    <li>Filtering: (2)(3)(4)(5)(6)(7) -> filters all prediction to remove false positives</li>
    <li>Scoring: (8) -> given the filtered prediction, gives an evaluation</li>
</ol>

<b> Clasp Model (1)</b>
We use ParameterGrid() to compute all the combination given the param_grid and we obtained <b>19</b> different models
<p>in: features ts [21][98][n] - out: prediction [21][98][m]</p>

In [ ]:
#all selected hyperparameters values to gridsearch
param_grid = {
    "window_size": ['suss'],
    "distance": ['euclidean_distance'],
    "score":['roc_auc','f1'],
    "early_stopping": [True,False],
    "k_neighbours":[1,3,5,7,9],
    "n_jobs":[4]
}


# len(ParameterGrid(param_grid)) = 20
for p_idx,params in enumerate(ParameterGrid(param_grid)):
    #excl_radius has to be larger than neighbours
    params["excl_radius"]=params["k_neighbours"]+2
    cpsl=[]
    for i in range(len(TIMESERIES)):
        df=ReadAndPreProcess(TIMESERIES[i])
        gt=LoadingGroundTruth(df,GROUNDTRUTH[i])
        cp_all,cps,clasp=GetClasp2(df,gt,list(range(len(features_name))),p_idx,i, **params)
        cpsl.append(cps)

    # COMMENTED TO AVOID OVERWRITE ALREADY COMPUTED FILE
    # save prediction of [20][21][98] = [param][video][feature]
    #with open("../cpsl_param_"+str(p_idx)+".pkl", "wb") as f:
        #pickle.dump(cpsl, f)


<b>Filtering (2)(3)(4)(5)(6)(7)</b>
The gridsearch isn't finished yet. Each step has its known set of parameters that needs to be found to have the optimal model. So in the filtering phase we gridsearch all values and generate all possible filtered prediction from each different. 

The computational costs is made by for loops:
<p>for each models = 19</p>
<p style="text-indent: 15px;">for each params = 243 </p>
<p style="text-indent: 30px;">for each videos = 21 </p>
<p style="text-indent: 45px;">for each features = 98</p>
<p>in:[20][21][98] - out:[20][21][c]</p>

In [ ]:
#load dataframe for 21 videos
with open("../dfl.pkl", "rb") as f:
    dfl = pickle.load(f)

#load groundtruth for 21 videos
with open("../gtl.pkl", "rb") as f:
    gtl = pickle.load(f)

In [ ]:
# From previous step, load 20 models in modelpred
modelpred=[]
for i in range(0,20):
    with open("../res/cpsl_param_"+str(i)+".pkl", "rb") as f:
        modelpred.append(pickle.load(f))

#20 model
#21 video
#98 feature

In [ ]:
#2. from 98 predictions, divide it into 6 groups
# Some prediction could be repeated in the groups
def SplitSaliency(pred):
    # 2. split features in 6 saliency groups
    # vel,acc,jerk,specific,generic
    # specific: other type of feature specific for that saliency
    # generic: other type of feature that describe the whole body movement
    ## generic features: 0,3
    ariel_el=[26,27,28,29,30,31,32,33,34,35,36,37,2,8,14,0,3]
    ariel = UnionCPS(*pred[ariel_el])
   
    strn_el=[38,39,40,41,42,43,44,45,46,47,48,49,1,9,0,3]
    strn = UnionCPS(*pred[strn_el])

    rhel_el=[50,51,52,53,54,55,56,57,58,59,60,61,7,11,16,17,18,21,0,3]
    rhel = UnionCPS(*pred[rhel_el])

    lhel_el=[62,63,64,65,66,67,68,69,70,71,72,73,6,10,16,17,19,20,0,3]
    lhel = UnionCPS(*pred[lhel_el])
    
    rplm_el=[74,75,76,77,78,79,80,81,82,83,84,85,5,13,15,23,25,0,3]
    rplm = UnionCPS(*pred[rplm_el])

    lplm_el=[86,87,88,89,90,91,92,93,94,95,96,97,4,12,15,22,24,0,3]
    lplm = UnionCPS(*pred[lplm_el])

    return [ariel,strn,rhel,lhel,rplm,lplm]

In [ ]:
# 3. given one list, determine the mean value in the group if it's within maj_margin
#    and decide if to compute the mean if the number of el in the group is over maj_thre
def CombineSingleSaliency(saliencies, maj_margin, maj_thre):
    res=[]
    for sal in saliencies:
        res.append(MajorityVoteCP(sal, maj_margin, maj_thre))
    return res
        


In [ ]:
# the filtering part for just one prediction.
# after we computed all prediction from 20 different models
# all prediction should be filtered to be combined and filtered to remove False Positive
# in: prediction
def PostFilterTogether(model_id,video_id,param_id,param_len,density,pred,gt, maj_margin, maj_thre, zone_margin, del_margin, dtw_threshold):
    """
        pred: 98 predictions of a single video
    """
    
    print(f"model:{model_id}/20 - video:{video_id}/21 - param:{param_id}/{param_len} - Start                                               ", end='\r')

    #2. from a list[98] divide it into 6 lists. Some prediction could be repeated into diff groups
    saliencies_raw = SplitSaliency(pred)
    print(f"model:{model_id}/20 - video:{video_id}/21 - param:{param_id}/{param_len} - Split Saliency completed                            ", end='\r')
    #3. each group has different list of prediction. combine it into 1 and apply majorityvote
    saliencies = CombineSingleSaliency(saliencies_raw,maj_margin,maj_thre)
    print(f"model:{model_id}/20 - video:{video_id}/21 - param:{param_id}/{param_len} - Combine Saliency completed                          ", end='\r')
    #4. from 6 list, combine into 1 list
    pred_united = UnionCPS(*saliencies)
    print(f"model:{model_id}/20 - video:{video_id}/21 - param:{param_id}/{param_len} - Union completed                                     ", end='\r')
    #5. there is no annotated zone. remove prediction from that subset
    pred_ignored = IgnoreZone(video_id,pred_united,gt,zone_margin)
    print(f"model:{model_id}/20 - video:{video_id}/21 - param:{param_id}/{param_len} - Ignore Zone completed                               ", end='\r')
    #6. apply motion fusion: in a group within del_margin, remove everything except 1 and last
    pred_del = delnear(pred_ignored,del_margin)
    print(f"model:{model_id}/20 - video:{video_id}/21 - param:{param_id}/{param_len} - delnear completed                                   ", end='\r')
    #7. check the results with DTW to remove potential FP
    pred_final=FPremoverDTW(density,pred_del,dtw_threshold)
    print(f"model:{model_id}/20 - param:{param_id}/{param_len} - video:{video_id}/21 - DTW completed                                       ", end='\r')
    # return a list of prediction
    return pred_final
    



In [ ]:
#Filtering part for all prediction from all 20 models
#gridsearch params for our filtering part
param_grid = {
    "maj_margin": [80,100,120],
    "maj_thre": [1,2,3],
    "zone_margin":[80,100,120],
    "del_margin": [80,100,120],
    "dtw_threshold":[80,100,120]
}



#for each model, for each params,
# compute for each video the filtering
# each leaf would be a prediction with a specific model and specific filter_param
model_res=[]
for model_id,model in enumerate(modelpred): #20 models predictions
    param_value=[]
    for p_idx,params in enumerate(ParameterGrid(param_grid)): #243
        video=[]
        for i in range(len(TIMESERIES)): #21 videos
            df = dfl[i]
            gt = gtl[i]
            res=PostFilterTogether(model_id,i,p_idx,len(ParameterGrid(param_grid)),df.iloc[:,3],np.array(model[i],dtype="object"),gt,params["maj_margin"],params["maj_thre"],params["zone_margin"],params["del_margin"],params["dtw_threshold"])
            video.append(res)
       
        param_value.append(video)
    model_res.append(param_value)

# COMMENTED TO AVOID OVERWRITE LOCAL FILES
# save the filtered prediction in local
#with open("../collection_models_prediction_filtered.pkl", "wb") as f:
#    pickle.dump(model_res, f)
    




'\nversione 1\nfisso param_grid\ncalcolo f1 score per only training fold\nprendo il migliore\ncalcolo per ogni singolo video nel validation\n\nfor model in models:\n    for param in paramgrid:\n        for fold in folds:\n            for ts in fold.train:\n                f1s_1 = compute single f1score \n                calcolo f1score per singolo ts\n            f1s_mean = compute mean f1score mean(f1s_1,f1s_1,...)\n            per un intero train_set ritorno lo il f1score medio\n        f1s_mean_mean = compute mean of f1s_mean(f1s_mean,f1s_mean,...)\n        per ogni train_set ritorno la media = come performa questo param across all folds\n    check best f1s_mean_mean\nper ogni param diverso, controllo quello che mi massimizza\nO(n^3)\n'

<b>Scoring (8)</b>
here we take as input all the filtered results and performs a cross-validation with our predictions to see which hyperparameters for our model+filter is the best and then test it on the validation set

In [30]:
# load the filtered prediction
with open("../collection_models_prediction_filtered.pkl", "rb") as f:
    collection_models_prediction_filtered = pickle.load(f)

In [ ]:
models=collection_models_prediction_filtered
# model:20 params:243 video:21

In [62]:
# Compute the f1 margin

# for each video i take all prediction for a particular video and create a single list
mean_win=[]
for i in range(0,21):
    pred_flat = []
    for model in models:
        for video in model:
            pred_flat = np.sort(np.append(pred_flat,video[i]).flatten())
            pred_flat = np.unique(pred_flat)

    df=ReadAndPreProcess(TIMESERIES[i])
    gt=LoadingGroundTruth(df,GROUNDTRUTH[i])
    
    for g in gt:
        pred_around=[]
        for p in pred_flat:
            if p > g and abs(p-g) > 150:
                idx_p=p
                break 

            if abs(g-p) <= 150:
                pred_around.append(p)
        
        if pred_around==[]:
            print("empty")
        else:
            #print(f'g:{g} mean:{statistics.mean(pred_around)} dist:{abs(g-statistics.mean(pred_around))}')
            mean_win.append(abs(g-statistics.mean(pred_around)))

print(statistics.mean(mean_win))



   






empty
26.835850373316887


In [ ]:
# LEAVE ONE VIDEO OUT - LOVO
f1_margin=100
scores=[]
for model_id,params in enumerate(models): #1 model = 243 params <- 20 model
    for p_idx,videos in enumerate(params): # 21 video = 1 param <- 243 params
        score_folds = []
        for video_idx in range(len(TIMESERIES)): # 1 prediction = 1 video <- 1 param = 21 video

            # single fold
            train_set = [i for i in range(len(TIMESERIES)) if i != video_idx]
            #test_set = video_idx
            score_singlefold_eachvideo=[]
            for ts in train_set:
                #get score each video for ts
                #compute score
                gt = gtl[ts]
                _,_,f1,_,_,_=f1scoremargin(gt,videos[ts],f1_margin)
                score_singlefold_eachvideo.append(f1)
            #media per training
            score_folds.append(statistics.mean(score_singlefold_eachvideo))
        

        scores.append({"model":model_id, "param":p_idx, "score":statistics.mean(score_folds)})

type_col=["model","param","score"]
resexcel=pd.DataFrame()
resexcel["type"]=type_col
best_models=[]
best_score=0
for i in scores:
    # if better, reset list and append
    if i["score"] > best_score:
        best_models=[]
        best_models.append(i)
    # if equal, append to the list
    elif i["score"] == best_score:
        best_models.append(i)
best_scores=[]
for best_idx,best in enumerate(best_models):
    best_score=[]
    for video_idx in range(len(TIMESERIES)):
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    best_scores.append({"model":model_id, "param":p_idx, "score":statistics.mean(best_score)})
    resexcel[best_idx]=[model_id,p_idx,statistics.mean(best_score)]

resexcel.to_excel("outputFile/LOVO.xlsx")
print("lovo")
for i in best_scores:
    print(i)






C:\Users\loluc\AppData\Local\Temp\ipykernel_2324\575830046.py:41: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  resexcel[best_idx]=[model_id,p_idx,statistics.mean(best_score)]
C:\Users\loluc\AppData\Local\Temp\ipykernel_2324\575830046.py:41: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  resexcel[best_idx]=[model_id,p_idx,statistics.mean(best_score)]
C:\Users\loluc\AppData\Local\Temp\ipykernel_2324\575830046.py:41: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times

lovo
{'model': 19, 'param': 242, 'score': 0.6819501062408826}
{'model': 19, 'param': 242, 'score': 0.6819501062408826}
{'model': 19, 'param': 242, 'score': 0.6811950473462889}
{'model': 19, 'param': 242, 'score': 0.6043582167862663}
{'model': 19, 'param': 242, 'score': 0.6032635260364032}
{'model': 19, 'param': 242, 'score': 0.6025085899156134}
{'model': 19, 'param': 242, 'score': 0.5061765160517547}
{'model': 19, 'param': 242, 'score': 0.5061765160517547}
{'model': 19, 'param': 242, 'score': 0.5054314100434908}
{'model': 19, 'param': 242, 'score': 0.6674359665576131}
{'model': 19, 'param': 242, 'score': 0.6675512528298209}
{'model': 19, 'param': 242, 'score': 0.6675512528298209}
{'model': 19, 'param': 242, 'score': 0.5795011975991052}
{'model': 19, 'param': 242, 'score': 0.5820877307361525}
{'model': 19, 'param': 242, 'score': 0.5820877307361525}
{'model': 19, 'param': 242, 'score': 0.5028519708597968}
{'model': 19, 'param': 242, 'score': 0.5061393820419449}
{'model': 19, 'param': 242

In [ ]:
# LEAVE ONE VIDEO OUT - LOVO
f1_margin=27
scores=[]
for model_id,params in enumerate(models): #1 model = 243 params <- 20 model
    for p_idx,videos in enumerate(params): # 21 video = 1 param <- 243 params
        score_folds = []
        for video_idx in range(len(TIMESERIES)): # 1 prediction = 1 video <- 1 param = 21 video

            # single fold
            train_set = [i for i in range(len(TIMESERIES)) if i != video_idx]
            #test_set = video_idx
            score_singlefold_eachvideo=[]
            for ts in train_set:
                #get score each video for ts
                #compute score
                gt = gtl[ts]
                _,_,f1,_,_,_=f1scoremargin(gt,videos[ts],f1_margin)
                score_singlefold_eachvideo.append(f1)
            #media per training
            score_folds.append(statistics.mean(score_singlefold_eachvideo))
        

        scores.append({"model":model_id, "param":p_idx, "score":statistics.mean(score_folds)})

type_col=["model","param","score"]
resexcel=pd.DataFrame()
resexcel["type"]=type_col
best_models=[]
best_score=0
for i in scores:
    # if better, reset list and append
    if i["score"] > best_score:
        best_models=[]
        best_models.append(i)
    # if equal, append to the list
    elif i["score"] == best_score:
        best_models.append(i)
best_scores=[]
for best_idx,best in enumerate(best_models):
    best_score=[]
    for video_idx in range(len(TIMESERIES)):
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    best_scores.append({"model":model_id, "param":p_idx, "score":statistics.mean(best_score)})
    resexcel[best_idx]=[model_id,p_idx,statistics.mean(best_score)]

resexcel.to_excel("outputFile/LOVO_27.xlsx")
print("lovo")
for i in best_scores:
    print(i)




In [ ]:
# LEAVE ONE DANCER OUT - LODO
CORA=[0,1,2,3,4]
MARIANNE=[5,6,7,8,9,10,11,12,13,14,15,16]
MURIEL=[17,18,19,20]

f1_margin=100
scores=[]
for model_id,params in enumerate(models): #1 model = 243 params <- 20 model
    for p_idx,videos in enumerate(params): # 21 video = 1 param <- 243 params
        score_folds = []
        
        #fold1
        TRAINING_1 = CORA+MARIANNE
        for ts in TRAINING_1:
            #get score each video for ts
            #compute score
            gt = gtl[ts]
            _,_,f1,_,_,_=f1scoremargin(gt,videos[ts],f1_margin)
            score_singlefold_eachvideo.append(f1)
        #media per training
        fold1_score = statistics.mean(score_singlefold_eachvideo)

        #fold2
        TRAINING_2 = CORA+MURIEL
        for ts in TRAINING_2:
            #get score each video for ts
            #compute score
            gt = gtl[ts]
            _,_,f1,_,_,_=f1scoremargin(gt,videos[ts],f1_margin)
            score_singlefold_eachvideo.append(f1)
        #media per training
        fold2_score = statistics.mean(score_singlefold_eachvideo)

        #fold3
        TRAINING_3 = MARIANNE+MURIEL
        for ts in TRAINING_3:
            #get score each video for ts
            #compute score
            gt = gtl[ts]
            _,_,f1,_,_,_=f1scoremargin(gt,videos[ts],f1_margin)
            score_singlefold_eachvideo.append(f1)
        #media per training
        fold3_score = statistics.mean(score_singlefold_eachvideo)

        training_mean_score = statistics.mean([fold1_score,fold2_score,fold3_score])
        scores.append({"model":model_id, "param":p_idx, "score":training_mean_score})

type_col=["model","param","score"]
resexcel=pd.DataFrame()
resexcel["type"]=type_col
best_models=[]
best_score=0
for i in scores:
    if i["score"] > best_score:
        best_models=[]
        best_models.append(i)
    if i["score"] == best_score:
        best_models.append(i)
best_scores=[]
for best_idx,best in enumerate(best_models):

    #fold1
    best_score=[]
    for video_idx in CORA:
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    fold1_score = statistics.mean(best_score)

    #fold2
    best_score=[]
    for video_idx in MARIANNE:
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    fold2_score = statistics.mean(best_score)

    #fold3
    best_score=[]
    for video_idx in MURIEL:
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    fold3_score = statistics.mean(best_score)

    val_mean_score = statistics.mean([fold1_score,fold2_score,fold3_score])
   
    best_scores.append({"model":model_id, "param":p_idx, "score":val_mean_score})
    resexcel[best_idx]=[model_id,p_idx,val_mean_score]

resexcel.to_excel("outputFile/LODO.xlsx")
print("lodo")
for i in best_scores:
    print(i)


type_col=["model","param","score"]
resexcel=pd.DataFrame()
resexcel["type"]=type_col
best_models=[]
best_score=0
for i in scores:
    # if better, reset list and append
    if i["score"] > best_score:
        best_models=[]
        best_models.append(i)
    # if equal, append to the list
    elif i["score"] == best_score:
        best_models.append(i)
best_scores=[]
for best_idx,best in enumerate(best_models):
    best_score=[]
    for video_idx in range(len(TIMESERIES)):
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    best_scores.append({"model":model_id, "param":p_idx, "score":statistics.mean(best_score)})
    resexcel[best_idx]=[model_id,p_idx,statistics.mean(best_score)]

resexcel.to_excel("outputFile/LOVO_NOFOLDS.xlsx")
print("lovo")
for i in best_scores:
    print(i)


C:\Users\loluc\AppData\Local\Temp\ipykernel_2324\1604486098.py:86: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  resexcel[best_idx]=[model_id,p_idx,val_mean_score]
C:\Users\loluc\AppData\Local\Temp\ipykernel_2324\1604486098.py:86: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  resexcel[best_idx]=[model_id,p_idx,val_mean_score]
C:\Users\loluc\AppData\Local\Temp\ipykernel_2324\1604486098.py:86: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor perfor

lodo
{'model': 19, 'param': 242, 'score': 0.6899653703327471}
{'model': 19, 'param': 242, 'score': 0.6899653703327471}
{'model': 19, 'param': 242, 'score': 0.6889082878803159}
{'model': 19, 'param': 242, 'score': 0.6229242052312273}
{'model': 19, 'param': 242, 'score': 0.6213916381814188}
{'model': 19, 'param': 242, 'score': 0.6203347276123131}
{'model': 19, 'param': 242, 'score': 0.5313658223874225}
{'model': 19, 'param': 242, 'score': 0.5313658223874225}
{'model': 19, 'param': 242, 'score': 0.530322673975853}
{'model': 19, 'param': 242, 'score': 0.6786258878889065}
{'model': 19, 'param': 242, 'score': 0.6787872886699975}
{'model': 19, 'param': 242, 'score': 0.6787872886699975}
{'model': 19, 'param': 242, 'score': 0.6102279471876104}
{'model': 19, 'param': 242, 'score': 0.6138490935794768}
{'model': 19, 'param': 242, 'score': 0.6138490935794768}
{'model': 19, 'param': 242, 'score': 0.5320905751632895}
{'model': 19, 'param': 242, 'score': 0.5366929508182968}
{'model': 19, 'param': 242,

In [ ]:
# LEAVE ONE DANCER OUT - LODO
CORA=[0,1,2,3,4]
MARIANNE=[5,6,7,8,9,10,11,12,13,14,15,16]
MURIEL=[17,18,19,20]

f1_margin=27
scores=[]
for model_id,params in enumerate(models): #1 model = 243 params <- 20 model
    for p_idx,videos in enumerate(params): # 21 video = 1 param <- 243 params
        score_folds = []
        
        #fold1
        TRAINING_1 = CORA+MARIANNE
        for ts in TRAINING_1:
            #get score each video for ts
            #compute score
            gt = gtl[ts]
            _,_,f1,_,_,_=f1scoremargin(gt,videos[ts],f1_margin)
            score_singlefold_eachvideo.append(f1)
        #media per training
        fold1_score = statistics.mean(score_singlefold_eachvideo)

        #fold2
        TRAINING_2 = CORA+MURIEL
        for ts in TRAINING_2:
            #get score each video for ts
            #compute score
            gt = gtl[ts]
            _,_,f1,_,_,_=f1scoremargin(gt,videos[ts],f1_margin)
            score_singlefold_eachvideo.append(f1)
        #media per training
        fold2_score = statistics.mean(score_singlefold_eachvideo)

        #fold3
        TRAINING_3 = MARIANNE+MURIEL
        for ts in TRAINING_3:
            #get score each video for ts
            #compute score
            gt = gtl[ts]
            _,_,f1,_,_,_=f1scoremargin(gt,videos[ts],f1_margin)
            score_singlefold_eachvideo.append(f1)
        #media per training
        fold3_score = statistics.mean(score_singlefold_eachvideo)

        training_mean_score = statistics.mean([fold1_score,fold2_score,fold3_score])
        scores.append({"model":model_id, "param":p_idx, "score":training_mean_score})

type_col=["model","param","score"]
resexcel=pd.DataFrame()
resexcel["type"]=type_col
best_models=[]
best_score=0
for i in scores:
    if i["score"] > best_score:
        best_models=[]
        best_models.append(i)
    if i["score"] == best_score:
        best_models.append(i)
best_scores=[]
for best_idx,best in enumerate(best_models):

    #fold1
    best_score=[]
    for video_idx in CORA:
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    fold1_score = statistics.mean(best_score)

    #fold2
    best_score=[]
    for video_idx in MARIANNE:
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    fold2_score = statistics.mean(best_score)

    #fold3
    best_score=[]
    for video_idx in MURIEL:
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    fold3_score = statistics.mean(best_score)

    val_mean_score = statistics.mean([fold1_score,fold2_score,fold3_score])
   
    best_scores.append({"model":model_id, "param":p_idx, "score":val_mean_score})
    resexcel[best_idx]=[model_id,p_idx,val_mean_score]

resexcel.to_excel("outputFile/LODO_27.xlsx")
print("lodo")
for i in best_scores:
    print(i)


type_col=["model","param","score"]
resexcel=pd.DataFrame()
resexcel["type"]=type_col
best_models=[]
best_score=0
for i in scores:
    # if better, reset list and append
    if i["score"] > best_score:
        best_models=[]
        best_models.append(i)
    # if equal, append to the list
    elif i["score"] == best_score:
        best_models.append(i)
best_scores=[]
for best_idx,best in enumerate(best_models):
    best_score=[]
    for video_idx in range(len(TIMESERIES)):
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    best_scores.append({"model":model_id, "param":p_idx, "score":statistics.mean(best_score)})
    resexcel[best_idx]=[model_id,p_idx,statistics.mean(best_score)]

resexcel.to_excel("outputFile/LOVO_NOFOLDS_27.xlsx")
print("lovo")
for i in best_scores:
    print(i)


In [ ]:
# USE ALL TO BRUTE FORCE AND SCORING
f1_margin=100
scores=[]
for model_id,params in enumerate(models): #1 model = 243 params <- 20 model
    for p_idx,videos in enumerate(params): # 21 video = 1 param <- 243 params
        score_one = []
        for video_idx,video in enumerate(videos): # 1 prediction = 1 video <- 1 param = 21 video

      
            gt = gtl[video_idx]
            _,_,f1,_,_,_=f1scoremargin(gt,video,f1_margin)
            score_one.append(f1)
            

        scores.append({"model":model_id, "param":p_idx, "score":statistics.mean(score_one)})

type_col=["model","param","score"]
resexcel=pd.DataFrame()
resexcel["type"]=type_col
best_models=[]
best_score=0
for i in scores:
    # if better, reset list and append
    if i["score"] > best_score:
        best_models=[]
        best_models.append(i)
    # if equal, append to the list
    elif i["score"] == best_score:
        best_models.append(i)
best_scores=[]
for best_idx,best in enumerate(best_models):
    best_score=[]
    for video_idx in range(len(TIMESERIES)):
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    best_scores.append({"model":model_id, "param":p_idx, "score":statistics.mean(best_score)})
    resexcel[best_idx]=[model_id,p_idx,statistics.mean(best_score)]

resexcel.to_excel("outputFile/SCOREALL.xlsx")
print("lovo")
for i in best_scores:
    print(i)



In [ ]:
# USE ALL TO BRUTE FORCE AND SCORING
f1_margin=27
scores=[]
for model_id,params in enumerate(models): #1 model = 243 params <- 20 model
    for p_idx,videos in enumerate(params): # 21 video = 1 param <- 243 params
        score_one = []
        for video_idx,video in enumerate(videos): # 1 prediction = 1 video <- 1 param = 21 video

      
            gt = gtl[video_idx]
            _,_,f1,_,_,_=f1scoremargin(gt,video,f1_margin)
            score_one.append(f1)
            

        scores.append({"model":model_id, "param":p_idx, "score":statistics.mean(score_one)})

type_col=["model","param","score"]
resexcel=pd.DataFrame()
resexcel["type"]=type_col
best_models=[]
best_score=0
for i in scores:
    # if better, reset list and append
    if i["score"] > best_score:
        best_models=[]
        best_models.append(i)
    # if equal, append to the list
    elif i["score"] == best_score:
        best_models.append(i)
best_scores=[]
for best_idx,best in enumerate(best_models):
    best_score=[]
    for video_idx in range(len(TIMESERIES)):
        gt = gtl[video_idx]
        _,_,f1,_,_,_=f1scoremargin(gt,models[best["model"]][best["param"]][video_idx],f1_margin)
        best_score.append(f1)
    best_scores.append({"model":model_id, "param":p_idx, "score":statistics.mean(best_score)})
    resexcel[best_idx]=[model_id,p_idx,statistics.mean(best_score)]

resexcel.to_excel("outputFile/SCOREALL.xlsx")
print("lovo")
for i in best_scores:
    print(i)

